In [1]:
import numpy as np
import os
import glob
from PIL import Image
from time import time

In [2]:
%ls /work/cybai2020

PyTorch-StudioGAN/  hq_list_eval_partition.txt
celeba-hq/          list_eval_partition.txt


### Count number of train/valid/test in HQ version

In [3]:
%cat /work/cybai2020/list_eval_partition.txt

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [2]:
orig_partition_path = '/work/cybai2020/list_eval_partition.txt'

with open(orig_partition_path, 'r') as f:
    lines = f.readlines()
    part_map = np.empty([len(lines)]).astype(np.int32)
    for idx, line in enumerate(lines):
        part_map[idx] = int(line.split(' ')[-1])

In [8]:
celeba_hq_dir = '/work/cybai2020/celeba-hq'
hq_part_cnt = {0: 0, 1: 0, 2: 0}
hq_partition_path = '/work/cybai2020/hq_list_eval_partition.txt'

with open(os.path.join(data_dir, 'hq_list_eval_partition.txt'), 'w') as f:
    for idx, hq_img_name in enumerate(os.listdir(celeba_hq_dir)):
        
        start_t = time()
        
        img_idx = int(hq_img_name.split('.')[0][2:]) - 1
        hq_part_cnt[part_map[img_idx]] += 1
        f.write(f"{hq_img_name} {part_map[img_idx]}\n")

In [9]:
hq_part_cnt

{0: 24183, 1: 2993, 2: 2824}

In [3]:
img_dim = 64

celeba_hq_dir = '/work/cybai2020/celeba-hq'
data_dir = f'/home/cybai2020/work/PyTorch-StudioGAN/data/CELEBA-HQ_{img_dim}'

os.makedirs(os.path.join(data_dir, 'train/dummy_class'), exist_ok=True)
os.makedirs(os.path.join(data_dir, 'valid/dummy_class'), exist_ok=True)

ema_t = None
total_t = 0

for idx, hq_img_name in enumerate(os.listdir(celeba_hq_dir)):
        
    start_t = time()

    img_idx = int(hq_img_name.split('.')[0][2:]) - 1

    part_dir = 'train/dummy_class' if part_map[img_idx] == 0 else 'valid/dummy_class'
    write_dir = os.path.join(data_dir, part_dir)

    with Image.open(os.path.join(celeba_hq_dir, hq_img_name), 'r') as im:
        im = im.resize((img_dim, img_dim), resample=Image.BOX)
        im.save(os.path.join(write_dir, hq_img_name), "PNG")

    start_t = time() - start_t
    total_t += start_t

    if ema_t is None:
        ema_t = start_t
    else:
        ema_t = 0.9 * ema_t + 0.1 * start_t

    print(f"{idx + 1} / {30000} ({total_t:.2f} / {(29999 - idx) * ema_t:.2f})", end='\r')